In [1]:

import keras
from keras.layers import Activation, Dense, Input
from keras.layers import Conv2D, Flatten
from keras.layers import Reshape, Conv2DTranspose
from keras.layers import LeakyReLU
from keras.layers import BatchNormalization
from keras.optimizers import RMSprop
from keras.models import Model
from keras.datasets import mnist

import numpy as np
import math
import matplotlib.pyplot as plt

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function


def generator(inputs, image_size):
 
    image_resize = image_size // 4
    kernel_size = 5
    layer_filters = [128, 64, 32, 1]

    x = Dense(image_resize * image_resize * layer_filters[0])(inputs)
    x = Reshape((image_resize, image_resize, layer_filters[0]))(x)

    for filters in layer_filters:
        if filters > layer_filters[-2]:
            strides = 2
        else:
            strides = 1
        x = BatchNormalization()(x)
        x = Activation('relu')(x)
        x = Conv2DTranspose(filters=filters,
                            kernel_size=kernel_size,
                            strides=strides,
                            padding='same')(x)

    x = Activation('sigmoid')(x)
    generator = Model(inputs, x, name='generator')
    return generator


def discriminator(inputs):

    kernel_size = 5
    layer_filters = [32, 64, 128, 256]

    x = inputs
    for filters in layer_filters:
        if filters == layer_filters[-1]:
            strides = 1
        else:
            strides = 2
        x = LeakyReLU(alpha=0.2)(x)
        x = Conv2D(filters=filters,
                   kernel_size=kernel_size,
                   strides=strides,
                   padding='same')(x)

    x = Flatten()(x)
    x = Dense(1)(x)
    x = Activation('sigmoid')(x)
    discriminator = Model(inputs, x, name='discriminator')
    return discriminator


def train(models, x_train, params):

    generator, discriminator, adversarial = models
    batch_size, latent_size, train_steps = params
    save_interval = 1000
    noise_input = np.random.uniform(-1.0, 1.0, size=[16, latent_size])
    for i in range(train_steps):
        # Pick random real images
        rand_indexes = np.random.randint(0, x_train.shape[0], size=batch_size)
        train_images = x_train[rand_indexes]
        # Generate fake images
        noise = np.random.uniform(-1.0, 1.0, size=[batch_size, latent_size])
        fake_images = generator.predict(noise)
        x = np.concatenate((train_images, fake_images))
        # Label real and fake images
        y = np.ones([2 * batch_size, 1])
        y[batch_size:, :] = 0
        # Train the Discriminator network
        metrics = discriminator.train_on_batch(x, y)
        loss = metrics[0]
        acc = metrics[1]
        log = "%d: [discriminator loss: %f, acc: %f]" % (i, loss, acc)

        # Generate random noise
        noise = np.random.uniform(-1.0, 1.0, size=[batch_size, latent_size])
        # Label fake images as real
        y = np.ones([batch_size, 1])
        # Train the Adversarial network
        metrics = adversarial.train_on_batch(noise, y)
        loss = metrics[0]
        acc = metrics[1]
        log = "%s [adversarial loss: %f, acc: %f]" % (log, loss, acc)
        print(log)
        if (i + 1) % save_interval == 0:
            if (i + 1) == train_steps:
                show = True
            else:
                show = False
            plot_images(generator,
                        noise_input=noise_input,
                        show=show,
                        step=(i + 1))


def plot_images(generator,
                noise_input,
                show=False,
                step=0):

    filename = "mnist_dcgan_%d.png" % step
    images = generator.predict(noise_input)
    plt.figure(figsize=(2.4, 2.4))
    num_images = images.shape[0]
    image_size = images.shape[1]
    rows = int(math.sqrt(noise_input.shape[0]))
    for i in range(num_images):
        plt.subplot(rows, rows, i + 1)
        image = images[i, :, :, :]
        image = np.reshape(image, [image_size, image_size])
        plt.imshow(image, cmap='gray')
        plt.axis('off')
    plt.savefig(filename)
    if show:
        plt.show()
    else:
        plt.close('all')


# MNIST dataset
(x_train, _), (_, _) = mnist.load_data()

image_size = x_train.shape[1]
x_train = np.reshape(x_train, [-1, image_size, image_size, 1])
x_train = x_train.astype('float32') / 255

# The latent or z vector is 100-dim
latent_size = 100
batch_size = 64
train_steps = 40000
lr = 0.0002
decay = 6e-8
input_shape = (image_size, image_size, 1)

# Build Discriminator Model
inputs = Input(shape=input_shape, name='discriminator_input')
discriminator = discriminator(inputs)
# [1] uses Adam, but discriminator converges easily with RMSprop
optimizer = RMSprop(lr=lr, decay=decay)
discriminator.compile(loss='binary_crossentropy',
                      optimizer=optimizer,
                      metrics=['accuracy'])
discriminator.summary()

# Build Generator Model
input_shape = (latent_size, )
inputs = Input(shape=input_shape, name='z_input')
generator = generator(inputs, image_size)
generator.summary()

# Build Adversarial Model = Generator + Discriminator
optimizer = RMSprop(lr=lr*0.5, decay=decay*0.5)
discriminator.trainable = False
adversarial = Model(inputs, discriminator(generator(inputs)), name='dcgan')
adversarial.compile(loss='binary_crossentropy',
                    optimizer=optimizer,
                    metrics=['accuracy'])
adversarial.summary()

# Train Discriminator and Adversarial Networks
models = (generator, discriminator, adversarial)
parameters = (batch_size, latent_size, train_steps)
train(models, x_train, parameters)

Using TensorFlow backend.


11493376/11490434 [==============================] - 0s 0us/step
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
discriminator_input (InputLa (None, 28, 28, 1)         0         
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 28, 28, 1)         0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 14, 14, 32)        832       
_________________________________________________________________
leaky_re_lu_2 (LeakyReLU)    (None, 14, 14, 32)        0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 7, 7, 64)          51264     
_________________________________________________________________
leaky_re_lu_3 (LeakyReLU)    (None, 7, 7, 64)          0         
_________________________________________________________________
conv2d_3 (C

/usr/local/lib/python3.5/dist-packages/Keras-2.1.3-py3.5.egg/keras/engine/training.py:953: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?


0: [discriminator loss: 0.694636, acc: 0.234375] [adversarial loss: 0.966533, acc: 0.000000]
1: [discriminator loss: 0.653838, acc: 0.539062] [adversarial loss: 1.217487, acc: 0.000000]
2: [discriminator loss: 0.567038, acc: 0.898438] [adversarial loss: 1.629620, acc: 0.000000]
3: [discriminator loss: 0.461206, acc: 0.875000] [adversarial loss: 1.814973, acc: 0.000000]
4: [discriminator loss: 0.369090, acc: 0.992188] [adversarial loss: 3.449577, acc: 0.000000]
5: [discriminator loss: 0.319328, acc: 0.937500] [adversarial loss: 1.532195, acc: 0.000000]
6: [discriminator loss: 0.242540, acc: 1.000000] [adversarial loss: 3.659487, acc: 0.000000]
7: [discriminator loss: 0.194500, acc: 0.968750] [adversarial loss: 2.277316, acc: 0.000000]
8: [discriminator loss: 0.124037, acc: 0.984375] [adversarial loss: 2.543495, acc: 0.000000]
9: [discriminator loss: 0.085464, acc: 0.992188] [adversarial loss: 2.168370, acc: 0.000000]
10: [discriminator loss: 0.045257, acc: 1.000000] [adversarial loss: 2

88: [discriminator loss: 0.316488, acc: 0.960938] [adversarial loss: 2.335524, acc: 0.000000]
89: [discriminator loss: 0.353582, acc: 0.992188] [adversarial loss: 2.736315, acc: 0.000000]
90: [discriminator loss: 0.398812, acc: 0.914062] [adversarial loss: 1.813920, acc: 0.000000]
91: [discriminator loss: 0.335422, acc: 0.968750] [adversarial loss: 3.299269, acc: 0.000000]
92: [discriminator loss: 0.322575, acc: 0.890625] [adversarial loss: 1.185815, acc: 0.000000]
93: [discriminator loss: 0.411799, acc: 0.578125] [adversarial loss: 4.049617, acc: 0.000000]
94: [discriminator loss: 0.574574, acc: 0.718750] [adversarial loss: 0.868368, acc: 0.062500]
95: [discriminator loss: 0.535385, acc: 0.500000] [adversarial loss: 3.097690, acc: 0.000000]
96: [discriminator loss: 0.259015, acc: 0.921875] [adversarial loss: 1.893908, acc: 0.000000]
97: [discriminator loss: 0.215156, acc: 1.000000] [adversarial loss: 2.390841, acc: 0.000000]
98: [discriminator loss: 0.249763, acc: 0.984375] [adversari

...

39570: [discriminator loss: 0.512393, acc: 0.742188] [adversarial loss: 1.486201, acc: 0.171875]
39571: [discriminator loss: 0.535923, acc: 0.695312] [adversarial loss: 0.717648, acc: 0.546875]
39572: [discriminator loss: 0.592069, acc: 0.648438] [adversarial loss: 1.500468, acc: 0.234375]
39573: [discriminator loss: 0.555779, acc: 0.710938] [adversarial loss: 1.153823, acc: 0.390625]
39574: [discriminator loss: 0.513371, acc: 0.742188] [adversarial loss: 1.528326, acc: 0.218750]
39575: [discriminator loss: 0.570264, acc: 0.710938] [adversarial loss: 0.778595, acc: 0.515625]
39576: [discriminator loss: 0.555005, acc: 0.679688] [adversarial loss: 1.728113, acc: 0.125000]
39577: [discriminator loss: 0.583394, acc: 0.687500] [adversarial loss: 1.279742, acc: 0.328125]
39578: [discriminator loss: 0.451062, acc: 0.812500] [adversarial loss: 1.412901, acc: 0.234375]
39579: [discriminator loss: 0.514815, acc: 0.718750] [adversarial loss: 0.971828, acc: 0.406250]
39580: [discriminator loss: 0.

39657: [discriminator loss: 0.574835, acc: 0.718750] [adversarial loss: 1.711440, acc: 0.125000]
39658: [discriminator loss: 0.578873, acc: 0.726562] [adversarial loss: 1.126839, acc: 0.281250]
39659: [discriminator loss: 0.511030, acc: 0.765625] [adversarial loss: 1.402810, acc: 0.187500]
39660: [discriminator loss: 0.538375, acc: 0.726562] [adversarial loss: 1.458437, acc: 0.250000]
39661: [discriminator loss: 0.580651, acc: 0.695312] [adversarial loss: 1.227200, acc: 0.312500]
39662: [discriminator loss: 0.573610, acc: 0.734375] [adversarial loss: 1.332667, acc: 0.203125]
39663: [discriminator loss: 0.481202, acc: 0.757812] [adversarial loss: 1.169330, acc: 0.343750]
39664: [discriminator loss: 0.511481, acc: 0.718750] [adversarial loss: 1.300329, acc: 0.250000]
39665: [discriminator loss: 0.499925, acc: 0.781250] [adversarial loss: 1.169593, acc: 0.328125]
39666: [discriminator loss: 0.523860, acc: 0.726562] [adversarial loss: 1.331372, acc: 0.234375]
39667: [discriminator loss: 0.

39744: [discriminator loss: 0.502743, acc: 0.757812] [adversarial loss: 1.301360, acc: 0.234375]
39745: [discriminator loss: 0.517955, acc: 0.742188] [adversarial loss: 1.510862, acc: 0.187500]
39746: [discriminator loss: 0.540330, acc: 0.734375] [adversarial loss: 1.202872, acc: 0.281250]
39747: [discriminator loss: 0.515670, acc: 0.734375] [adversarial loss: 1.405183, acc: 0.265625]
39748: [discriminator loss: 0.469306, acc: 0.726562] [adversarial loss: 1.166463, acc: 0.375000]
39749: [discriminator loss: 0.509508, acc: 0.773438] [adversarial loss: 1.450547, acc: 0.171875]
39750: [discriminator loss: 0.502824, acc: 0.726562] [adversarial loss: 1.191985, acc: 0.281250]
39751: [discriminator loss: 0.532705, acc: 0.726562] [adversarial loss: 1.087852, acc: 0.375000]
39752: [discriminator loss: 0.471528, acc: 0.765625] [adversarial loss: 1.617075, acc: 0.171875]
39753: [discriminator loss: 0.496287, acc: 0.750000] [adversarial loss: 1.315206, acc: 0.328125]
39754: [discriminator loss: 0.

39831: [discriminator loss: 0.511388, acc: 0.765625] [adversarial loss: 1.246344, acc: 0.281250]
39832: [discriminator loss: 0.515434, acc: 0.757812] [adversarial loss: 1.409238, acc: 0.218750]
39833: [discriminator loss: 0.483806, acc: 0.796875] [adversarial loss: 1.294938, acc: 0.250000]
39834: [discriminator loss: 0.557869, acc: 0.710938] [adversarial loss: 1.237707, acc: 0.296875]
39835: [discriminator loss: 0.462850, acc: 0.820312] [adversarial loss: 1.142877, acc: 0.375000]
39836: [discriminator loss: 0.530201, acc: 0.718750] [adversarial loss: 1.818046, acc: 0.078125]
39837: [discriminator loss: 0.542398, acc: 0.695312] [adversarial loss: 1.122123, acc: 0.406250]
39838: [discriminator loss: 0.526271, acc: 0.742188] [adversarial loss: 1.934231, acc: 0.078125]
39839: [discriminator loss: 0.501607, acc: 0.757812] [adversarial loss: 1.214492, acc: 0.390625]
39840: [discriminator loss: 0.571159, acc: 0.726562] [adversarial loss: 1.672873, acc: 0.140625]
39841: [discriminator loss: 0.

39918: [discriminator loss: 0.558282, acc: 0.710938] [adversarial loss: 1.208322, acc: 0.343750]
39919: [discriminator loss: 0.521150, acc: 0.703125] [adversarial loss: 2.246150, acc: 0.062500]
39920: [discriminator loss: 0.572632, acc: 0.664062] [adversarial loss: 1.253141, acc: 0.281250]
39921: [discriminator loss: 0.493080, acc: 0.750000] [adversarial loss: 1.625711, acc: 0.156250]
39922: [discriminator loss: 0.515174, acc: 0.750000] [adversarial loss: 1.350376, acc: 0.250000]
39923: [discriminator loss: 0.493641, acc: 0.742188] [adversarial loss: 1.218123, acc: 0.234375]
39924: [discriminator loss: 0.545869, acc: 0.742188] [adversarial loss: 1.555065, acc: 0.156250]
39925: [discriminator loss: 0.535021, acc: 0.734375] [adversarial loss: 1.455467, acc: 0.281250]
39926: [discriminator loss: 0.445231, acc: 0.765625] [adversarial loss: 1.145151, acc: 0.296875]
39927: [discriminator loss: 0.541040, acc: 0.718750] [adversarial loss: 1.637443, acc: 0.156250]
39928: [discriminator loss: 0.